# ⚛️ Simulación de Dinámica Molecular con OpenMM en Google Colab

Este cuaderno guía el proceso completo de **preparación y simulación de un sistema proteico** (por ejemplo, un complejo proteína–nanobody) usando **OpenMM**. Está diseñado para ejecutarse paso a paso, desde la preparación de la estructura hasta la generación de la trayectoria de dinámica molecular.

---

## 📌 Flujo del análisis y función de cada celda

1. **Instalación de librerías (Celda 1 y 2)**  
   - Instala las librerías necesarias:  
     - `openmm` → motor de simulación.  
     - `pdbfixer` → preparación de estructuras.  
     - `biopython` → conversión de archivos CIF a PDB.  
     - `py3Dmol` → visualización 3D interactiva.  
   - ⚠️ En Colab se requiere un reinicio automático del kernel (ya gestionado en el script). Después de este reinicio, continuar directamente en la celda “Paso B”.

2. **Conversión de estructura (Celda 3)**  
   - Permite subir un archivo en formato **CIF** (por ejemplo, generado en AlphaFold o RCSB PDB).  
   - Lo convierte automáticamente en **PDB**, que es el formato estándar para simulaciones en OpenMM.

3. **Preparación del sistema (Celda 4)**  
   - Limpia y centra el complejo proteico.  
   - Añade **hidrógenos** y ajusta el pH fisiológico (7.4).  
   - Añade **solvente (agua TIP3P)** e **iones** para neutralizar la carga.  
   - Aplica el campo de fuerza **Amber14**.  
   - Guarda el sistema preparado como `protein_system_CORRECTED.pdb`.

4. **Configuración y ejecución de la simulación (Celda 5)**  
   - Define los parámetros de la simulación (temperatura, integrador, paso de tiempo).  
   - Selecciona la **plataforma de ejecución** (CUDA u OpenCL si hay GPU, o CPU en su defecto).  
   - Ejecuta tres fases:  
     - **Minimización de energía** → eliminar choques iniciales.  
     - **Equilibrado** → estabilizar la temperatura y presión.  
     - **Producción** → simulación de 10 ns (5,000,000 pasos de 2 fs).  
   - Guarda la trayectoria en formato `.dcd`.

5. **Descarga de resultados (Celda 6)**  
   - Permite descargar:  
     - `protein_system_CORRECTED.pdb` → estructura inicial del sistema preparado.  
     - `trajectory.dcd` → trayectoria completa de la simulación (coordenadas de todos los átomos a lo largo del tiempo).

---

## 📊 Resultados esperados
- **Trayectoria MD en formato `.dcd`** lista para análisis (RMSD, contactos, energía libre, etc.).  
- **Sistema inicial `.pdb`** correctamente preparado con solvente e iones.  
- **Logs de simulación** con temperatura, energía potencial y velocidad.  

---

➡️ En conjunto, este cuaderno permite pasar **de una estructura cruda (CIF)** a una **simulación de dinámica molecular de 10 ns**, todo dentro de Google Colab y sin necesidad de instalación local.


In [ ]:
# --- Celda 1 Instalar librerías para la simulación y el manejo de archivos PDB/CIF ---
print("Instalando OpenMM para la simulación...")
!pip install openmm &> /dev/null

print("Instalando PDBFixer para preparar la estructura...")
!pip install pdbfixer &> /dev/null

print("Instalando BioPython para la conversión de CIF a PDB...")
!pip install biopython &> /dev/null

print("Instalando py3Dmol para la visualización 3D...")
!pip install py3Dmol &> /dev/null

print("\n¡Instalación completada!")

Instalando OpenMM para la simulación...
Instalando PDBFixer para preparar la estructura...
Instalando BioPython para la conversión de CIF a PDB...
Instalando py3Dmol para la visualización 3D...

¡Instalación completada!


In [ ]:
# --- Celda 2: Instalación y Reinicio Forzado ---
print("Instalando todas las librerías necesarias...")
!pip install openmm pdbfixer biopython py3Dmol &> /dev/null
print("¡Instalación completada!")
print("\n!!! ACCIÓN REQUERIDA !!!")
print("El entorno se reiniciará ahora. Después del reinicio, NO vuelvas a ejecutar esta celda.")
print("Continúa con la celda que te he proporcionado como 'Paso B'.")

# Esta línea reinicia el kernel de Python, que es más limpio que un colapso.
import os
os.kill(os.getpid(), 9)

Instalando todas las librerías necesarias...


In [ ]:
# --- Celda 3: Subir y Convertir (Post-Reinicio) ---
from google.colab import files
from Bio.PDB import MMCIFParser, PDBIO
import os

# Subir el archivo .cif
print("Por favor, selecciona de nuevo tu archivo .cif:")
uploaded = files.upload()
cif_filename = list(uploaded.keys())[0]
print(f"Archivo '{cif_filename}' subido.")

# Convertir a .pdb
pdb_filename = "protein.pdb"
print(f"Convirtiendo '{cif_filename}' a '{pdb_filename}'...")
parser = MMCIFParser(QUIET=True)
structure = parser.get_structure("alphafold_structure", cif_filename)
io = PDBIO()
io.set_structure(structure)
io.save(pdb_filename)
print("¡Conversión completada!")

Por favor, selecciona de nuevo tu archivo .cif:


Saving fold_2025_07_18_13_00_model_0.cif to fold_2025_07_18_13_00_model_0.cif
Archivo 'fold_2025_07_18_13_00_model_0.cif' subido.
Convirtiendo 'fold_2025_07_18_13_00_model_0.cif' a 'protein.pdb'...
¡Conversión completada!


In [ ]:
# --- Celda 4 de Preparación (Versión CORRECTA y Definitiva) ---
print("--- Iniciando preparación del sistema (método robusto) ---")

from openmm.app import *
from openmm import *
from openmm.unit import *
from sys import stdout
import numpy as np

# 'pdb_filename' debería existir desde la celda de conversión anterior
if 'pdb_filename' not in locals():
    pdb_filename = "protein.pdb" # Fallback por si acaso

try:
    print(f"\n[Paso 1/4] Cargando la estructura desde '{pdb_filename}'...")
    pdb = PDBFile(pdb_filename)
    modeller = Modeller(pdb.topology, pdb.positions)
    forcefield = ForceField('amber14-all.xml', 'amber14/tip3p.xml')
    print("Campo de fuerza cargado.")

    print(f"\n[Paso 2/4] Centrando el complejo y añadiendo hidrógenos...")
    positions_nm = np.array(modeller.positions.value_in_unit(nanometer))
    center = positions_nm.mean(axis=0)
    modeller.positions -= center * nanometer
    modeller.addHydrogens(forcefield, pH=7.4)
    print("Complejo centrado e hidrogenado.")

    print(f"\n[Paso 3/4] Añadiendo solvente (agua) e iones...")
    modeller.addSolvent(forcefield, padding=1.0*nanometer, model='tip3p')
    modeller.addExtraParticles(forcefield)
    print("Solvente e iones añadidos.")

    final_pdb_filename = 'protein_system_CORRECTED.pdb'
    PDBFile.writeFile(modeller.topology, modeller.positions, open(final_pdb_filename, 'w'))
    print(f"Sistema final y CORRECTO guardado en '{final_pdb_filename}'.")

    print(f"\n[Paso 4/4] Creando el sistema de OpenMM...")
    system = forcefield.createSystem(modeller.topology, nonbondedMethod=PME,
            nonbondedCutoff=1.0*nanometer, constraints=HBonds)

    print("\n¡Preparación del sistema completada con éxito!")

except Exception as e:
    print(f"\nOcurrió un error durante la preparación: {e}")

--- Iniciando preparación del sistema (método robusto) ---

[Paso 1/4] Cargando la estructura desde 'protein.pdb'...
Campo de fuerza cargado.

[Paso 2/4] Centrando el complejo y añadiendo hidrógenos...
Complejo centrado e hidrogenado.

[Paso 3/4] Añadiendo solvente (agua) e iones...
Solvente e iones añadidos.
Sistema final y CORRECTO guardado en 'protein_system_CORRECTED.pdb'.

[Paso 4/4] Creando el sistema de OpenMM...

¡Preparación del sistema completada con éxito!


In [ ]:
# --- Celda 5 SIMULACION de Minimización, Equilibrado y Producción 10 ns---
print("--- Iniciando la simulación de Dinámica Molecular ---")

# --- Paso 1: Configurar la simulación ---
# El Integrador define cómo se actualizan las posiciones y velocidades en cada paso de tiempo.
# Usamos un LangevinIntegrator, que es bueno para mantener la temperatura constante (termostato).
integrator = LangevinIntegrator(300*kelvin, 1/picosecond, 2*femtoseconds)

# La plataforma indica dónde se ejecutará la simulación.
# Intentamos usar la GPU ('CUDA' o 'OpenCL') que es mucho más rápida. Si no, usa la CPU.
try:
    platform = Platform.getPlatformByName('CUDA')
    properties = {'CudaPrecision': 'mixed'}
    print("Plataforma de simulación: CUDA (GPU)")
except Exception:
    try:
        platform = Platform.getPlatformByName('OpenCL')
        properties = {'OpenCLPrecision': 'mixed'}
        print("Plataforma de simulación: OpenCL (GPU)")
    except Exception:
        platform = Platform.getPlatformByName('CPU')
        properties = {}
        print("Plataforma de simulación: CPU")


# El objeto 'Simulation' une todo: topología, sistema, integrador y plataforma.
simulation = Simulation(modeller.topology, system, integrator, platform, properties)

# Asignamos las posiciones iniciales (las que preparamos en la celda anterior)
simulation.context.setPositions(modeller.positions)
print("Configuración de la simulación completada.")


# --- Paso 2: Minimización de Energía ---
print("\nPaso 2: Minimizando la energía del sistema...")
simulation.minimizeEnergy()
print("Minimización completada.")


# --- Paso 3: Equilibrado y Producción ---
# Configuramos los "reporteros", que son los encargados de guardar los datos.
# Guardaremos datos cada 1000 pasos (equivalente a 2 ps).
report_interval = 1000

# Reportero para mostrar el progreso en la pantalla
simulation.reporters.append(StateDataReporter(stdout, report_interval, step=True,
        potentialEnergy=True, temperature=True, progress=True, remainingTime=True,
        speed=True, totalSteps=5000000, separator='\t'))

# Reportero para guardar la trayectoria (los movimientos) en un archivo .dcd
# Guardaremos 500 ps de simulación (250,000 pasos * 2 fs/paso)
simulation.reporters.append(DCDReporter('trajectory.dcd', report_interval))
print("\nReporteros configurados. La simulación de producción comenzará ahora.")
print("Esto puede tardar varios minutos...")


# ¡Ejecutamos la simulación!
# 500,000 pasos con un paso de tiempo de 2 fs nos dan 1 nanosegundo (ns) de simulación.
# Para una prueba rápida, usamos 250,000 pasos (500 picosegundos).
# Puedes aumentar este número para una simulación más larga.
# ¡Ejecutamos la simulación!
# 2,500,000 pasos con un paso de tiempo de 2 fs nos dan 5 nanosegundos (ns) de simulación.
simulation.step(5000000)


print("\n\n¡SIMULACIÓN COMPLETADA!")

Se han truncado las últimas 5000 líneas del flujo de salida.
0.1%	4000	-367479.7595935706	296.27218733467134	152	1:34:45
0.1%	5000	-368031.48014716594	297.93418657148027	156	1:32:26
0.1%	6000	-367545.8443354126	301.75927838530947	158	1:30:50
0.1%	7000	-366735.5402327366	302.21330786933976	160	1:29:49
0.2%	8000	-367199.779022702	299.99361549885424	161	1:29:06
0.2%	9000	-367871.30605889997	302.92977312381515	162	1:28:42
0.2%	10000	-367692.4232859574	300.25502695706456	163	1:28:17
0.2%	11000	-367625.55316398735	299.3675623366142	163	1:28:00
0.2%	12000	-367394.91035853606	299.33408112463735	164	1:27:41
0.3%	13000	-368126.00254336675	298.7024841984426	164	1:27:34
0.3%	14000	-367972.4546606324	298.37193551387867	163	1:27:54
0.3%	15000	-367700.0908239456	298.67441100481864	163	1:28:12
0.3%	16000	-367532.03055748413	298.7759171868229	162	1:28:20
0.3%	17000	-367051.3850042224	299.7052570405158	163	1:28:11
0.4%	18000	-368093.2808533518	302.4108477930236	163	1:28:01
0.4%	19000	-367045.538844184	3

In [ ]:
# --- Celda 6 Descagr de resultados ---
from google.colab import files

print("Descargando el archivo de topología/estructura inicial...")
files.download('protein_system_CORRECTED.pdb')

print("\nDescargando el archivo de trayectoria...")
files.download('trajectory.dcd')

Descargando el archivo de topología/estructura inicial...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>


Descargando el archivo de trayectoria...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>